In [ ]:
include("PWE.jl")

using Plots

In [ ]:
V0=5      # eV
kappa=0.5 # 1/nm
r0=0.5    # nm

ltype="square"

a=1.0
Gmax=40.0/a

Gset=generate_G_set_2D(ltype,Gmax,a)
VG=eval_atomic_VG_2D(Gset,eval_VPC(ltype,a),V0,kappa,r0)

In [ ]:
kpath,klen,kticks=generate_BZ_path(ltype,50,a)

E=eval_bands(kpath,Gset,VG)

plt=plot(klen,E[:,1],xticks=kticks)
for i in 2:10
  plot!(plt,klen,E[:,i])
end
display(plt)

In [ ]:
kx,ky,E=eval_bands_grid(-pi/a,+pi/a,50,Gset,VG)

display(surface(kx,ky,E[:,:,1]))
display(contourf(kx,ky,E[:,:,1],levels=20,color=:turbo,aspect_ratio=:equal))

In [ ]:
k=[0.0,0.0]
Hmtx=eval_Hmtx(k,Gset,VG,[[0.0,0.0]],1e-3)
eigval,eigvec=eigen(Hmtx)

N=100
x=LinRange(-a/2,+a/2,N)
y=LinRange(-a/2,+a/2,N)

In [ ]:
Psi=eval_Psi(x,y,Gset,eigvec[:,1])
display(heatmap(x,y,abs2.(Psi)',color=:turbo,aspect_ratio=:equal))

rng=maximum(abs.(Psi))
display(plot(heatmap(x,y,real.(Psi)',clims=(-rng,+rng),color=:coolwarm,aspect_ratio=:equal),
             heatmap(x,y,imag.(Psi)',clims=(-rng,+rng),color=:coolwarm,aspect_ratio=:equal)))

In [ ]:
kset,wght=generate_iBZ_covering(ltype,100,a)

println("iBZ points:",size(kset,1))

@time Eband=eval_bands(kset,Gset,VG)

In [ ]:
Emin=minimum(Eband[:,1])-0.1
Emax=maximum(Eband[:,2])+0.1
NE=500
E=LinRange(Emin,Emax,NE)

DOS=zeros(NE)

sigma=0.001

for b in 1:10
for i in 1:NE
  DOS[i]+=sum(wght.*exp.(-(E[i].-Eband[:,b]).^2 ./(2*sigma^2)))/(sqrt(2*pi)*sigma)
end
end

plot(E,DOS)